In [1]:
import pickle
import os
import sys
sys.path.append('../get_label_data')

from prepare_clients import prepare_clients
from prepare_matrikkel_objects import prepare_matrikkel_context, prepare_Kommune

In [2]:
username='untnu_matrikkel_muldan'
password='MatIndEcol2023'
[client, client_objects, clientKodelister, clientKommune] = prepare_clients(username, password)[0:4]

### read in the Trondheim pickle

In [3]:
file_location = os.path.dirname(os.path.dirname(os.getcwd())) \
                    + '/data/raw/matrikkel_data/building_pickles/' \
                    + '5001_Trondheim_116103_buildings_fetched_24.2.15.16.33.pkl'
#file = open(file_location, 'rb')
with open(file_location, 'rb') as file:
    description, building_objects = pickle.load(file)
print(description)
file.close()

{'number of objects': 116103, 'municipal_id': 5001, 'municipal_name': 'Trondheim', 'date extracted': '24.2.15.16.33', 'matrikkel_version': '2024-01-31T12:10:11Z'}


In [85]:
#building_objects['item'][1000]

#### extract matrikkl objects fro building object

create a matrikkel context so we can fetch objects with that matrikkel context

In [36]:
matrikkel_version = '2024-03-09T12:10:11Z'
timestamp,matrikkel_context = prepare_matrikkel_context(matrikkel_version, client_purpose='testi', client = client)


{'name': 'BruksenhetId', 'value': 549647570}


get a (or all) use units (dwellings?) from that building

In [69]:
def get_use_units(building_object, n_units) -> list:
    use_unit_ids = building_object['bruksenhetIds']['item']
    # limit number of units to n_units - first ones get used
    if len(use_unit_ids) > n_units:
        use_unit_ids = use_unit_ids[0:n_units]
    # prepare suds objects instead of dictionaries
    use_unit_ids_objects = [client.factory.create('ns7:BruksenhetId') for i in range(len(use_unit_ids))]
    for i, use_unit_id in enumerate(use_unit_ids):
        use_unit_ids_objects[i]['value'] = use_unit_id['value']
    use_unit_id_list = client.factory.create('ns7:BruksenhetIdList')
    use_unit_id_list['item'] = use_unit_ids_objects
    #print(use_unit_id_list)
    # request the use units
    use_units = [client_objects.service.getObject(use_unit_id, matrikkel_context)
                 for use_unit_id in use_unit_id_list['item']]
    # fetching multiple at the same time doesn't work...
    #use_units = client_objects.service.getObjects(use_unit_id_list, matrikkel_context)
    #print(use_units)
    return use_units
for i in range(10):
    try:
        use_units = get_use_units(building_objects['item'][i], 1000)
        #print(use_units)
    except:
        pass
use_units = get_use_units(building_objects['item'][1], 1000)
#use_units

In [87]:
def get_matrikkel_unit(use_unit):
    matrikkel_unit_id = use_unit['matrikkelenhetId']
    return client_objects.service.getObject(matrikkel_unit_id, matrikkel_context)

def check_for_annlegg_projeskjon_in_matrikkel_units(use_units):
    matrikkel_unit_id = use_unit['matrikkelenhetId']
    matrikkel_unit = client_objects.service.getObject(matrikkel_unit_id, matrikkel_context)
    if matrikkel_unit.__class__.__name__ == 'Seksjon':
        if matrikkel_unit['anleggsprojeksjonsflaterForMatrikkelenhet'] != '':
            return matrikkel_unit['anleggsprojeksjonsflaterForMatrikkelenhet']
    return False

for use_unit in use_units:
    matrikkel_unit = get_matrikkel_unit(use_unit)
    print(check_for_annlegg_projeskjon_in_matrikkel_units(use_unit))
    print(f'we get an object of type {matrikkel_unit.__class__.__name__}, with id {matrikkel_unit["id"]["value"]}')
    #print(matrikkel_unit['id']['value'])
matrikkel_unit = get_matrikkel_unit(use_units[0])
print(matrikkel_unit)

False
we get an object of type Seksjon, with id 560627005
False
we get an object of type Seksjon, with id 560627012
False
we get an object of type Seksjon, with id 560627004
False
we get an object of type Seksjon, with id 560627013
False
we get an object of type Seksjon, with id 560627007
False
we get an object of type Seksjon, with id 560626652
False
we get an object of type Seksjon, with id 560627006
False
we get an object of type Seksjon, with id 560627018
False
we get an object of type Seksjon, with id 560627017
False
we get an object of type Seksjon, with id 560627003
False
we get an object of type Seksjon, with id 560627019
False
we get an object of type Seksjon, with id 560627011
False
we get an object of type Seksjon, with id 560627010
False
we get an object of type Seksjon, with id 560627009
False
we get an object of type Seksjon, with id 560626653
False
we get an object of type Seksjon, with id 560627021
False
we get an object of type Seksjon, with id 560626654
False
we get a

In [77]:
def get_teiger(matrikkel_unit):
    teiger_given = matrikkel_unit['teigerForMatrikkelenhet']
    if teiger_given is None or teiger_given == '':
        print(f'no teiger, just None or empty')
        return None
    teigIds = [teig['teigId'] for teig in matrikkel_unit['teigerForMatrikkelenhet']['item'] if type(teig !=str)]
    teiger = [client_objects.service.getObject(teiger_id, matrikkel_context)
              for teiger_id in teigIds]
    teigId_list = client.factory.create('ns28:TeigIdList')
    teigId_list['item'] = teigIds
    teiger = client_objects.service.getObjects(teigId_list, matrikkel_context)
    return teiger
teiger = get_teiger(matrikkel_unit)

no teiger, just None or empty


In [31]:
def get_teig_boundary(teig):
    grense_linje_Ids = [i['grenselinjeId'] for i in teig['flate']['exterior']['curveDirections']['item']]
    grense_linjer = [client_objects.service.getObject(i, matrikkel_context) for i in grense_linje_Ids]
    print(grense_linjer)
    start_point_Ids = [i['kurve']['startpunktId'] for i in grense_linjer]
    stop_point_Ids = [i['kurve']['endpunktId'] for i in grense_linjer]
    start_points = [client_objects.service.getObject(i, matrikkel_context) for i in start_point_Ids]
    stop_points = [client_objects.service.getObject(i, matrikkel_context) for i in stop_point_Ids]
    return [[start,stop] for start, stop in zip(start_points, stop_points)]
    
start_stop_points = get_teig_boundary(teig)

[(Teiggrense){
   id = 
      (TeiggrenseId){
         value = 278276055
      }
   metadata = 
      (Metadata){
         item[] = 
            "oppdatertAv",
            "datafangstDato",
            "id",
            "uuid",
            "hjelpelinjetypeId",
            "avsluttetAv",
            "oppdateringsdato",
            "kurve",
            "omtvistet",
            "lagretNoyaktighetsklasseId",
            "versjonId",
            "administrativGrenseKodeId",
            "sluttdato",
            "versjon",
            "kommunalTilleggsdel",
            "kvalitet",
            "folgerTerrengdetaljId",
      }
   oppdateringsdato = 
      (Timestamp){
         timestamp = 2020-06-17 18:52:14.073000+02:00
      }
   sluttdato = 
      (Timestamp){
         timestamp = 9999-01-01 00:00:00+01:00
      }
   versjonId = 5
   oppdatertAv = "smatmynd"
   versjon = 1592412734073
   kurve = 
      (Arc){
         metadata = 
            (Metadata){
               item[] = 
             

## print location of building on mp

In [81]:
import pyproj
import folium

def show_building_and_teig(building_object, m):
    # prepare matrikkel context:
    matrikkel_version = '2024-03-09T12:10:11Z'
    timestamp,matrikkel_context = prepare_matrikkel_context(matrikkel_version, client_purpose='testi', client = client)

    # get the use unit id
    use_unit_id = building_object['bruksenhetIds']['item'][0]
    # make it into a suds object
    BruksenhetId = client.factory.create('ns7:BruksenhetId')
    BruksenhetId['value'] = use_unit_id['value']
    use_unit = client_objects.service.getObject(BruksenhetId, matrikkel_context)

    # get the matrikkel unit id
    matrikkel_unit_id = use_unit['matrikkelenhetId']
    matrikkel_unit = client_objects.service.getObject(matrikkel_unit_id, matrikkel_context)
    # the matrikkel unit actually kinda is the grunneiendom...
    # we take the main teig of the matrikkel unit
    print(matrikkel_unit['teigerForMatrikkelenhet'])
    teiger = matrikkel_unit['teigerForMatrikkelenhet']['item']
    for teig in teiger:
        if teig['hovedteig']:
            Main_teig_id  = teig['teigId']
            break
    ### ignore this and lets just do all teigs
    teiger = [client_objects.service.getObject(teig['teigId'], matrikkel_context) for teig in teiger]
    def get_teig_boundary_points(teig):
        grense_linje_Ids = [i['grenselinjeId'] for i in teig['flate']['exterior']['curveDirections']['item']]
        grense_linjer = [client_objects.service.getObject(i, matrikkel_context) for i in grense_linje_Ids]
        #print(grense_linjer)
        start_point_Ids = [i['kurve']['startpunktId'] for i in grense_linjer]
        stop_point_Ids = [i['kurve']['endpunktId'] for i in grense_linjer]
        start_points = [client_objects.service.getObject(i, matrikkel_context) for i in start_point_Ids]
        stop_points = [client_objects.service.getObject(i, matrikkel_context) for i in stop_point_Ids]
        return [[start,stop] for start, stop in zip(start_points, stop_points)]
    
    start_stop_points = [get_teig_boundary_points(teig) for teig in teiger]

    # Define the coordinate systems
    utm32n = pyproj.CRS("EPSG:25832")  # EUREF89 UTM Sone 32
    wgs84 = pyproj.CRS("EPSG:4326")  # Latitude/longitude

    def add_marker_from_building(building_object,m):
        x = building_object['representasjonspunkt']['position']['x']
        y = building_object['representasjonspunkt']['position']['y']
        transformer = pyproj.Transformer.from_crs(utm32n, wgs84, always_xy=True)
        lon, lat = transformer.transform(x, y)
        folium.Marker([lat, lon]).add_to(m)

    def add_line_between_two_points(start_point, stop_point, m):
        x1 = start_point['posisjon']['x']
        y1 = start_point['posisjon']['y']
        x2 = stop_point['posisjon']['x']
        y2 = stop_point['posisjon']['y']
        transformer = pyproj.Transformer.from_crs(utm32n, wgs84, always_xy=True)
        lon1, lat1 = transformer.transform(x1, y1)
        lon2, lat2 = transformer.transform(x2, y2)
        folium.PolyLine([[lat1, lon1], [lat2, lon2]], color='blue').add_to(m)

    # add the building to the map
    add_marker_from_building(building_object,m)
    # add the teig to the map
    for start_stop_point in start_stop_points:
        for start, stop in start_stop_point:
            add_line_between_two_points(start, stop, m)
    return m


# Create a map centered at Trondheim
m = folium.Map(location=[63.4305, 10.3951], zoom_start=10)
for building in building_objects['item'][6:8]:
    m = show_building_and_teig(building, m)
#m = show_building_and_teig(building_objects['item'][2], m)
m

(TeigForMatrikkelenhetList){
   item[] = 
      (TeigForMatrikkelenhet){
         metadata = 
            (Metadata){
               item[] = 
                  "uuid",
                  "oppdatertAv",
                  "oppdateringsdato",
                  "teigId",
                  "sluttdato",
                  "id",
                  "avsluttetAv",
                  "versjonId",
                  "hovedteig",
            }
         oppdateringsdato = 
            (Timestamp){
               timestamp = 2020-06-18 02:30:04.470000+02:00
            }
         sluttdato = 
            (Timestamp){
               timestamp = 9999-01-01 00:00:00+01:00
            }
         versjonId = 2
         oppdatertAv = "smatmynd"
         id = 552063170
         hovedteig = True
         teigId = 
            (TeigId){
               value = 552063142
            }
         uuid = 
            (UUID){
               navnerom = "https://data.geonorge.no/matrikkel"
               uuid = "c3df2db3

In [33]:
import pyproj
import folium

# Define the coordinate systems
utm32n = pyproj.CRS("EPSG:25832")  # EUREF89 UTM Sone 32
wgs84 = pyproj.CRS("EPSG:4326")  # Latitude/longitude

def add_marker_from_building(building_object,m):
    x = building_object['representasjonspunkt']['position']['x']
    y = building_object['representasjonspunkt']['position']['y']
    transformer = pyproj.Transformer.from_crs(utm32n, wgs84, always_xy=True)
    lon, lat = transformer.transform(x, y)
    folium.Marker([lat, lon]).add_to(m)

def add_marker_from_grense_point(grense_point):
    x = grense_point['posisjon']['x']
    y = grense_point['posisjon']['y']
    transformer = pyproj.Transformer.from_crs(utm32n, wgs84, always_xy=True)
    lon, lat = transformer.transform(x, y)
    folium.Marker([lat, lon]).add_to(m)

def add_line_between_two_points(start_point, stop_point, m):
    x1 = start_point['posisjon']['x']
    y1 = start_point['posisjon']['y']
    x2 = stop_point['posisjon']['x']
    y2 = stop_point['posisjon']['y']
    transformer = pyproj.Transformer.from_crs(utm32n, wgs84, always_xy=True)
    lon1, lat1 = transformer.transform(x1, y1)
    lon2, lat2 = transformer.transform(x2, y2)
    folium.PolyLine([[lat1, lon1], [lat2, lon2]], color='blue').add_to(m)
# Create a map centered at Trondheim
m = folium.Map(location=[63.4305, 10.3951], zoom_start=10)

# Add markers for each building object
for building_object in building_objects['item'][9:10]:
    add_marker_from_building(building_object,m)
#add_marker_from_grense_point(start_point)
for start, stop in start_stop_points:
    add_line_between_two_points(start, stop, m)
# Display the map
m

In [26]:
import pyproj
import folium

# Define the coordinate systems
utm32n = pyproj.CRS("EPSG:25832")  # EUREF89 UTM Sone 32
wgs84 = pyproj.CRS("EPSG:4326")  # Latitude/longitude

def add_marker_from_building(building_object,m):
    x = building_object['representasjonspunkt']['position']['x']
    y = building_object['representasjonspunkt']['position']['y']
    transformer = pyproj.Transformer.from_crs(utm32n, wgs84, always_xy=True)
    lon, lat = transformer.transform(x, y)
    folium.Marker([lat, lon]).add_to(m)

# Create a map centered at Trondheim
m = folium.Map(location=[63.4305, 10.3951], zoom_start=10)

# Add markers for each building object
for building_object in building_objects['item'][9:10]:
    add_marker_from_building(building_object,m)

# Display the map
m

In [ ]:
import pyproj
import folium

# Define the coordinate systems
utm32n = pyproj.CRS("EPSG:25832")  # EUREF89 UTM Sone 32
wgs84 = pyproj.CRS("EPSG:4326")  # Latitude/longitude

# Get the coordinates from the matrikkel item
x = building_objects['item'][2]['representasjonspunkt']['position']['x']
y = building_objects['item'][2]['representasjonspunkt']['position']['y']

# Convert the coordinates
transformer = pyproj.Transformer.from_crs(utm32n, wgs84, always_xy=True)
lon, lat = transformer.transform(x, y)

# Create a map centered at the coordinates
m = folium.Map(location=[lat, lon], zoom_start=11)

# Add a marker at the coordinates
folium.Marker([lat, lon]).add_to(m)

# Display the map
m

## print codes for matrikkel

In [10]:
allCodes = clientKodelister.service.getKodelister(timestamp,matrikkel_context)
print(allCodes)

(KodelisteTransfer){
   kodelisterIds = 
      (KodelisteIdList){
         item[] = 
            (KodelisteId){
               value = 1
            },
            (KodelisteId){
               value = 2
            },
            (KodelisteId){
               value = 3
            },
            (KodelisteId){
               value = 4
            },
            (KodelisteId){
               value = 5
            },
            (KodelisteId){
               value = 6
            },
            (KodelisteId){
               value = 7
            },
            (KodelisteId){
               value = 8
            },
            (KodelisteId){
               value = 9
            },
            (KodelisteId){
               value = 10
            },
            (KodelisteId){
               value = 11
            },
            (KodelisteId){
               value = 12
            },
            (KodelisteId){
               value = 13
            },
            (KodelisteId){
             

In [11]:
print(client_objects)


Suds ( https://fedorahosted.org/suds/ )  version: 1.1.2

Service ( StoreServiceWS ) tns="http://matrikkel.statkart.no/matrikkelapi/wsapi/v1/service/store"
   Prefixes (40)
      ns0 = "http://matrikkel.statkart.no/matrikkelapi/wsapi/v1/domain"
      ns1 = "http://matrikkel.statkart.no/matrikkelapi/wsapi/v1/domain/adresse"
      ns2 = "http://matrikkel.statkart.no/matrikkelapi/wsapi/v1/domain/adresse/koder"
      ns3 = "http://matrikkel.statkart.no/matrikkelapi/wsapi/v1/domain/aktivitetsliste"
      ns4 = "http://matrikkel.statkart.no/matrikkelapi/wsapi/v1/domain/aktivitetsliste/koder"
      ns5 = "http://matrikkel.statkart.no/matrikkelapi/wsapi/v1/domain/bruker"
      ns6 = "http://matrikkel.statkart.no/matrikkelapi/wsapi/v1/domain/bruker/koder"
      ns7 = "http://matrikkel.statkart.no/matrikkelapi/wsapi/v1/domain/bygning"
      ns8 = "http://matrikkel.statkart.no/matrikkelapi/wsapi/v1/domain/bygning/koder"
      ns9 = "http://matrikkel.statkart.no/matrikkelapi/wsapi/v1/domain/elektr